In [3]:
import pandas as pd
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException
from selenium.common.exceptions import StaleElementReferenceException, TimeoutException

In [4]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

chrome_options = Options()
chrome_options.add_argument("--headless")      #run without opening window
chrome_options.add_argument("--disable-gpu")   #run without opening window

In [5]:
flight_days_col, origin_IATA, origin_airport, durations, destinations, flights_a_day, airlines=[],[],[],[],[],[],[]

In [ ]:
driver = webdriver.Chrome()
driver.maximize_window()
url = 'https://www.flightsfrom.com/top-100-airports-in-europe'
driver.get(url)
wait = WebDriverWait(driver, 10)

In [ ]:
table = wait.until(EC.presence_of_element_located((By.XPATH, "/html/body/div[1]/div[2]/div/div/div[1]/div[2]/div/div")))
rows = table.find_elements(By.CLASS_NAME, "hometoplist-item")

In [ ]:
for i in range(50):
    try:
        rows = driver.find_elements(By.CLASS_NAME, "hometoplist-item")  # Re-locate the elements in each iteration
        temp = rows[i].find_element(By.CLASS_NAME, "makebluehighlight")
        current_airport_city=rows[i].find_element(By.CLASS_NAME, "hometoplist-first").text[:-6]
        current_airport_code=rows[i].find_element(By.CLASS_NAME, "hometoplist-first").text[-4:-1]
        link = rows[i].get_attribute("href")
        rows[i].click()

        try:
            accept_btn = wait.until(EC.element_to_be_clickable((By.XPATH, '/html/body/div[5]/div[2]/div/span[2]/button')))
            accept_btn.click()
        except TimeoutException:
            pass

        #here,we are moving to the specific airport page
        # Wait for the content to load
        flights = WebDriverWait(driver, 10)
        wait.until(EC.presence_of_element_located((By.CLASS_NAME, 'ff-list-stats')))
        try:
            show_all_button = driver.find_element(By.CLASS_NAME, "ff-show-all")
            show_all_button.click()
        except NoSuchElementException:
            pass
        specific_element = driver.find_element(By.CLASS_NAME, "ff-content")
        html = specific_element.get_attribute('innerHTML')
        soup = BeautifulSoup(html, 'html.parser')

        # Find elements by class name
        elements = soup.find_all(class_='ff-li-list')
        for element in elements:
            # Extract the flight duration
            duration_element = element.select_one('.ff-row-text-durationnr')
            duration = duration_element.text if duration_element else None
            durations.append(duration)
            # Extract the text from the flight days and store in a list
            container_element = element.find(class_='uk-flex')
            days_elements = container_element.find_all(class_='flightsfrom-list-days')
            flight_days = [day.text for day in days_elements if 'disabled' not in day.get('class', [])]
            flight_days_col.append(flight_days)
            # Extract the flights per day
            flights_per_day_element = element.select_one('.ff-flights-daily')
            flights_per_day = flights_per_day_element.text if flights_per_day_element else None
            flights_a_day.append(flights_per_day)
            # Extract the destination
            destination_element = element.select_one('.ff-row-name a')
            destination = destination_element.text if destination_element else None
            destinations.append((destination))

            airline_count_element = element.select_one('.ff-row-airline .ff-image-wrap .flightsfrom-list-airline-ball')
            airline_count = airline_count_element.text if airline_count_element else None
            airline_count = int(airline_count) + 1 if airline_count else 1
            airlines.append(airline_count)
            origin_IATA.append(current_airport_code)
            origin_airport.append(current_airport_city)

        driver.back()
    except StaleElementReferenceException:
        # Handle the stale element reference exception, such as by refreshing the page or waiting for a specific condition
        driver.refresh()
driver.quit()        

In [ ]:
data={"Origin":origin_airport,
      "Origin IATA":origin_IATA,
      "Destination":destinations,
      "Flight_duratin":durations,
      "Flights_per_day":flights_a_day,
      "Operating airlines":airlines,
      "Flight days":flight_days_col}
df = pd.DataFrame(data)
df.to_csv('file1.csv', index=False)

In [9]:
df

Origin Origin_IATA                         Destination  \
0             Amsterdam         AMS                      CPH Copenhagen   
1             Amsterdam         AMS                          LHR London   
2             Amsterdam         AMS                          DUB Dublin   
3             Amsterdam         AMS                       BCN Barcelona   
4             Amsterdam         AMS                          LCY London   
5             Amsterdam         AMS                           CDG Paris   
6             Amsterdam         AMS                          BER Berlin   
7             Amsterdam         AMS                       FRA Frankfurt   
8             Amsterdam         AMS                          MUC Munich   
9             Amsterdam         AMS                      MAN Manchester   
10            Amsterdam         AMS                          LGW London   
11            Amsterdam         AMS                          LIS Lisbon   
12            Amsterdam         AMS                          ZRH Zurich   
13            Amsterdam         AMS                            OSL Oslo   
14            Amsterdam         AMS                       ARN Stockholm   
15            Amsterdam         AMS                          GVA Geneva   
16            Amsterdam         AMS                          MAD Madrid   
17            Amsterdam         AMS                          VIE Vienna   
18            Amsterdam         AMS                          AGP Malaga   
19            Amsterdam         AMS                         BRS Bristol   
20            Amsterdam         AMS                           LIN Milan   
21            Amsterdam         AMS                          WAW Warsaw   
22            Amsterdam         AMS                            FCO Rome   
23            Amsterdam         AMS                      BHX Birmingham   
24            Amsterdam         AMS     BSL Basel, Switzerland/Mulhouse   
25            Amsterdam         AMS                          LTN London   
26            Amsterdam         AMS                          PRG Prague   
27            Amsterdam         AMS                         HAM Hamburg   
28            Amsterdam         AMS                           MXP Milan   
29            Amsterdam         AMS                        HEL Helsinki   
30            Amsterdam         AMS                       EDI Edinburgh   
31            Amsterdam         AMS                            NCE Nice   
32            Amsterdam         AMS                       STR Stuttgart   
33            Amsterdam         AMS                      DUS Dusseldorf   
34            Amsterdam         AMS                      GOT Gothenburg   
35            Amsterdam         AMS                        IST Istanbul   
36            Amsterdam         AMS                        JFK New York   
37            Amsterdam         AMS                        FLR Florence   
38            Amsterdam         AMS                       OTP Bucharest   
39            Amsterdam         AMS                   TLV Tel Aviv-Yafo   
40            Amsterdam         AMS                          VCE Venice   
41            Amsterdam         AMS                        ABZ Aberdeen   
42            Amsterdam         AMS                          ATH Athens   
43            Amsterdam         AMS                       SVG Stavanger   
44            Amsterdam         AMS                        ALC Alicante   
45            Amsterdam         AMS                         BLL Billund   
46            Amsterdam         AMS                        BUD Budapest   
47            Amsterdam         AMS                        VLC Valencia   
48            Amsterdam         AMS                         GLA Glasgow   
49            Amsterdam         AMS               PMI Palma de Mallorca   
50            Amsterdam         AMS                         ATL Atlanta   
51            Amsterdam         AMS                         BLQ Bologna   
52            Amsterdam         AMS       